# Histogram APs

In [ ]:
import sys
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt

triskele_path = Path('../triskele/python/')
sys.path.append(str(triskele_path.resolve()))
import triskele

In [ ]:
# Specific Utils

def DFC_filter(raster):
    raster[raster > 1e4] = raster[raster < 1e4].max()

def show(im, im_size=1, save=None):
    plt.figure(figsize=(16*im_size,3*im_size))
    plt.imshow(im)
    plt.colorbar()
    
    if save is not None:
        plt.savefig(save, bbox_inches='tight', pad_inches=1)
    
    plt.show()

def mshow(Xs, titles=None, im_size=1, save=None):
    s = len(Xs)

    plt.figure(figsize=(16*im_size,3*im_size*s))

    for i in range(s):
        plt.subplot(s,1,i+1)
        plt.imshow(Xs[i])
        
        if titles is not None:
            plt.title(titles[i])
            
        plt.colorbar()
    
    if save is not None:
        plt.savefig(save, bbox_inches='tight', pad_inches=1)
        
    plt.show()

## Load a single raster

In [ ]:
raster_p = Path('../Data/phase1_rasters/Intensity_C3/UH17_GI3F051_TR.tif')
raster   = triskele.read(raster_p)
DFC_filter(raster)

In [ ]:
show(raster)

## Compute attributes

In [ ]:
area = np.array([25, 100, 500, 1e3, 5e3, 10e3, 50e3, 100e3, 150e3])

t = triskele.Triskele(raster, verbose=False)
attributes = t.filter(tree='tos-tree',
                      area=area
                     )
attributes.shape

In [ ]:
figs = list()
for i in range(attributes.shape[2]):
    figs.append(attributes[:,:,i])
    
mshow(figs)

In [ ]:
a = attributes
i = 3
show(a[:,:,i].astype(np.float) - a[:,:,i+1])

## Compute patches

In [ ]:
def create_patches(array, patch_size=3):
    amp = int((patch_size - 1 ) / 2)

    stack = list()
    for i in range(-amp, amp+1):
        ai = i if i > 0 else None
        bi = i if i < 0 else None
        ci = -bi if bi is not None else None
        di = -ai if ai is not None else None

        for j in range(-amp, amp+1):
            offset = np.zeros(array.shape)
            aj = j if j > 0 else None
            bj = j if j < 0 else None
            cj = -bj if bj is not None else None
            dj = -aj if aj is not None else None
            print('{}:{} {}:{} - {}:{} {}:{}'.format(ai, bi, ci, di, aj, bj, cj, dj))
            offset[ai:bi, aj:bj] = array[ci:di, cj:dj]
            stack.append(offset)
    return np.stack(stack, axis=-1)

offset_stack = create_patches(attributes, 5)
offset_stack.shape

In [ ]:
offset_stack[-2,-3,:].reshape(-1,1)

In [ ]:
stack_std = np.std(offset_stack, axis=-1)
stack_std.shape

In [ ]:
figs = list()
ttls = list()
for d in range(stack_std.shape[-1]):
    if d == 0:
        ttls.append('Origin')
    else:
        ttls.append('STD 5x5 from area {}'.format(area[d-1]))
    figs.append(stack_std[:,:,d])
    
mshow(figs, ttls, 2)

In [ ]:
stack_mean = np.mean(offset_stack, axis=-1)
stack_avr  = np.average(offset_stack, axis=-1)
stack_var  = np.var(offset_stack, axis=-1)
stack_min  = np.min(offset_stack, axis=-1)
stack_max  = np.max(offset_stack, axis=-1)

In [ ]:
size = '{}x{}'.format(patch_size, patch_size)
figs = [raster,
        stack_avr,
        stack_mean,
        stack_min,
        stack_max,
        stack_var,
        stack_std
       ]
ttls = ['Origin',
        'Average ' + size,
        'Mean ' + size,
        'Minimum ' + size,
        'Maximum ' + size,
        'Variance ' + size,
        'STD ' + size
       ]
mshow(figs, ttls)

In [ ]:
size = '{}x{}'.format(patch_size, patch_size)
figs = [raster,
        stack_avr[:,:,-1],
        stack_mean[:,:,-1],
        stack_min[:,:,-1],
        stack_max[:,:,-1],
        stack_var[:,:,-1],
        stack_std[:,:,-1]
       ]
ttls = ['Origin',
        'Average ' + size,
        'Mean ' + size,
        'Minimum ' + size,
        'Maximum ' + size,
        'Variance ' + size,
        'STD ' + size
       ]
mshow(figs, ttls, 2, save='mstack2.png')